In [1]:
import os
import sys
import numpy as np
import pandas as pd
pd.set_option('display.max_columns', 50)

from matplotlib import pyplot as plt
import seaborn as sns
%matplotlib inline

import plotly
import plotly.graph_objs as go
import cufflinks as cf
cf.set_config_file(offline=True)

In [2]:
base_path = os.path.abspath('../..')
data_path = os.path.join(base_path, 'data')
database_path = os.path.join(data_path, 'database')
strategy_path = os.path.join(base_path, 'strategy')
check_path = os.path.join(strategy_path, 'check')
sys.path.append(strategy_path)

In [3]:
from strategy import CommodityStrategy, EquityStrategy, IRStrategy, EmergingStrategy
from tester import Tester

In [4]:
from EMDY import EMDY
from EMPE import EMPE
from EMPM import EMPM
from EMSS import EMSS
from EMCA import EMCA

In [5]:
# EM equity data
emindex = pd.read_csv(os.path.join(data_path, 'totindex-em.csv'), header=0, index_col=0, parse_dates=True)
emindex1 = pd.read_csv(os.path.join(data_path, 'priceindex-em.csv'), header=0, index_col=0, parse_dates=True)
emfut = pd.read_csv(os.path.join(data_path, 'fut1return-em.CSV'), header=0, index_col=0, parse_dates=True)

total_em_ret = emindex.pct_change()
prc_em_ret = emindex1.pct_change()
fut_em_ret = emfut.pct_change()
fut_em_ret = fut_em_ret.reindex(pd.date_range(fut_em_ret.index[0], fut_em_ret.index[-1], freq ='B')) # bizday로 변환

prc_em_ret.loc[total_em_ret.index] = total_em_ret
raw_index = pd.concat([emindex1.loc[:'2012-12-31'], emfut.loc['2013-01-01':]]).iloc[1:]
EMRet = pd.concat([prc_em_ret.loc[:'2012-12-31'], fut_em_ret.loc['2013-01-01':]]).iloc[1:]

EMRet.fillna(0, inplace = True)
EMindex = EMRet
EMindex.iloc[0] = 0
EMindex = (1+ EMindex).cumprod()
EMindex = EMindex / EMindex.iloc[0]

raw_index.index.name = 'tdate'
raw_index.columns.name = 'ticker'

EMindex.index.name = 'tdate'
EMRet.index.name = 'tdate'

EMindex.columns.name = 'ticker'
EMRet.columns.name = 'ticker'

raw_index = pd.read_csv(os.path.join(data_path,'priceindex-mon-em.csv') ,header=0, index_col=0, parse_dates=True)
raw_index.index.name = 'tdate'
raw_index.columns.name = 'ticker'

In [6]:
r_data = (1.+ EMRet.loc[start_date:end_date]).cumprod()
db_data = (1.+ emss.ret.loc[start_date:end_date]).cumprod()

for column in EMindex.columns:
    toplot = r_data[column].to_frame()
    toplot['DB'] = db_data[column]
    toplot['DIFF'] = toplot[column] - toplot['DB']
    toplot.plot(figsize=(15,10), secondary_y='DIFF')

NameError: name 'start_date' is not defined

### EM 수치도 조금 차이난다.

# 1. EMDY

In [5]:
emdy = EMDY(strategy_name="EMDY", asset_type="EMERGING")
emdy.load_index_and_return(from_db=True, save_file=True)
emdy.load_strategy_data1(table='DS', origin1='EPS-em', origin2='EPS1-em')
emdy.load_strategy_data2(table='bloom', origin='10Yield-em')


BLOOM_EQUITY_GROUP = ['SA', 'ID', 'IN', 'MY', 'MX', 'KR', 'CN', 'BR', 'RU', 'TW']
bloom_raw_query = "SELECT * FROM GRP_RAW_INDEX WHERE TICKER IN {}".format(tuple(BLOOM_EQUITY_GROUP))

bloom = emdy.engine.execute(bloom_raw_query)
rows = [row for row in bloom]
columns = bloom.keys()
df_bloom = pd.DataFrame(rows, columns=columns)
df_bloom = df_bloom[df_bloom['field'] == 'RAW_INDEX']

df_bloom_pivot = df_bloom.pivot(index='tdate', columns='ticker', values='value')
df_bloom_pivot.index = [index for index in df_bloom_pivot.index]
emdy.raw_index = emdy.rename_columns(df_bloom_pivot, EmergingStrategy.BLOOM_EMERGING_COLUMNS)
emdy.raw_index = emdy.raw_index.resample("B").last()
emdy.raw_index.index.name = 'tdate'
emdy.raw_index.columns.name = 'ticker'


print(emdy.raw_index.tail())


2020-02-07 17:11:03,845 - EMDY - INFO - [STEP 0] START LOGGING EMDY
2020-02-07 17:11:03,849 - EMDY - INFO - [STEP 1] LOAD DATA
2020-02-07 17:11:03,850 - EMDY - INFO - [STEP 1 - 1] CONNECT TO BLOOM DATABASE
2020-02-07 17:11:03,863 - EMDY - INFO - [STEP 1 - 3] CHANGE BLOOM AND PAST DATA INTO STANDARD FORMAT
2020-02-07 17:11:05,970 - EMDY - INFO - [STEP 1 - 3] CHANGE BLOOM DATA INTO STANDARD FORMAT
2020-02-07 17:11:08,019 - EMDY - INFO - [STEP 1 - 3] CHANGE BLOOM DATA INTO STANDARD FORMAT
2020-02-07 17:11:22,927 - EMDY - INFO - [STEP 1 - 4] MERGE BLOOM AND PAST DATA
2020-02-07 17:11:22,939 - EMDY - INFO - [STEP 1 - 5] SAVE RETURN DATA INTO CSV FORMAT


ticker                BR         CN           ID           IN          KR  \
2020-01-28  3.674928e+11  85.222000  7241.309082  1378.645996  693.596008   
2020-01-29  3.645839e+11  83.866997  7239.845215  1384.875977  697.117004   
2020-01-30  3.651954e+11  81.975998  7152.706055  1372.359009  683.447021   
2020-01-31  3.593451e+11  81.348999  6970.068848  1358.072998  674.325989   
2020-02-03  3.616756e+11  81.650002  6902.028809  1331.053955  676.218994   

ticker                MX          MY           RU           SA          TW  
2020-01-28  41313.054688  532.872986  1379.264038  1331.144043  464.372986  
2020-01-29  41759.054688  532.416992  1382.739014  1351.140991  464.372986  
2020-01-30  41495.343750  530.877991  1369.197998  1359.339966  438.054993  
2020-01-31  40731.035156  525.250000  1352.081055  1339.985962  441.605988  
2020-02-03  40731.035156  521.802002  1348.333984  1338.228027  437.069000  


In [17]:
# raw_index =  emdy.raw_index.copy()

In [6]:
# emdy.raw_index.index.name = 'tdate'
# emdy.raw_index.columns.name = 'ticker'

In [7]:
# emdy.raw_index = raw_index.copy()
emdy.set_rebalance_period(ts_freq='month', cs_freq='month')
emdy.calculate_signal(CS=0.35, nopos=0.4, minobs1=12, minobs=60, IDN='out')

2020-02-07 17:11:36,786 - EMDY - INFO - [STEP 2] SET REBALANCE PERIOD
D:\projects\Polygon\works\grp\risk_premia\python\strategy\EMDY.py:72: FutureWarning:


Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/indexing.html#deprecate-loc-reindex-listlike

D:\projects\Polygon\works\grp\risk_premia\python\strategy\EMDY.py:73: FutureWarning:


Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/indexing.html#deprecate-loc-reindex-listlike



In [8]:

emdy.set_rebalance_period(ts_freq='month', cs_freq='month')
emdy.calculate_signal(CS=0.35, nopos=0.4, minobs1=12, minobs=60, IDN='out')
emdy.set_portfolio_parameter(cs_strategy_type='notional')
emdy.make_portfolio()

2020-02-07 17:11:43,786 - EMDY - INFO - [STEP 2] SET REBALANCE PERIOD
2020-02-07 17:11:45,466 - EMDY - INFO - [STEP 4] SET PORTFOLIO PARAMETER
2020-02-07 17:11:45,467 - EMDY - INFO - [STEP 5] MAKE PORTFOLIO
2020-02-07 17:11:45,467 - EMDY - INFO - [STEP 5 - 1] CALCULATE VOLATILITY
2020-02-07 17:12:24,999 - EMDY - INFO - [STEP 5 - 2] MAKE TS POSITION
2020-02-07 17:12:25,000 - EMDY - INFO - [STEP 5 - 2 - 1] ALIGN TS POSITION WITH REBALANCE DAY
2020-02-07 17:12:40,857 - EMDY - INFO - [STEP 5 - 2 - 2] TARGET VOL CONTROL to TS POSITION
2020-02-07 17:12:40,866 - EMDY - INFO - [STEP 5 - 2 - 3] STRATEGY LEVEL VOL CONTROL to TS POSITION
2020-02-07 17:12:42,042 - EMDY - INFO - [STEP 5 - 2 - 4] MAKE FINAL TS POSITION
2020-02-07 17:12:42,045 - EMDY - INFO - [STEP 5 - 3] MAKE CS POSITION
2020-02-07 17:12:42,045 - EMDY - INFO - [STEP 5 - 3 - 1] NO TARGET VOL CONTROL to CS POSITION
2020-02-07 17:12:42,046 - EMDY - INFO - [STEP 5 - 3 - 2] ALIGN CS POSITION WITH REBALANCE DAY
2020-02-07 17:12:46,607 - E

In [10]:
start_date = '2006-01-01'
end_date = '2018-05-09'

# get r results
emdy_comp_df = pd.read_csv('./past/emdy.csv', header=0, index_col=0, parse_dates=True)
emdy_lag_comp_df = pd.read_csv('./past/emdy_lag.csv', header=0, index_col=0, parse_dates=True)

In [11]:
tester = Tester(emdy)
tester.set_period(start=start_date, end=end_date)
tester.run(save_file=False, use_bt=False)

2020-02-07 17:12:54,242 - EMDY - INFO - [STEP 6] START BACKTEST
2020-02-07 17:12:54,243 - EMDY - INFO - [STEP 6 - 1] BACKTEST EMDY TIME SERIES
2020-02-07 17:12:54,997 - EMDY - INFO - [STEP 6 - 2] BACKTEST EMDY CROSS SECTIONAL


In [12]:
to_plot = (1.+ emdy_lag_comp_df).loc[start_date:].cumprod()
to_plot['TS_python'] = tester.strategy.TS_result
to_plot['CS_python'] = tester.strategy.CS_result
to_plot.iplot()

# 2. EMPE

In [17]:
empe = EMPE(strategy_name="EMPE", asset_type="EMERGING")
empe.load_index_and_return(from_db=True, save_file=True)
empe.load_strategy_data1(table='DS', origin1='EPS-em', origin2='EPS1-em')
empe.load_strategy_data2(table='bloom', origin='10Yield-em')


BLOOM_EQUITY_GROUP = ['SA', 'ID', 'IN', 'MY', 'MX', 'KR', 'CN', 'BR', 'RU', 'TW']
bloom_raw_query = "SELECT * FROM GRP_RAW_INDEX WHERE TICKER IN {}".format(tuple(BLOOM_EQUITY_GROUP))

bloom = empe.engine.execute(bloom_raw_query)
rows = [row for row in bloom]
columns = bloom.keys()
df_bloom = pd.DataFrame(rows, columns=columns)
df_bloom = df_bloom[df_bloom['field'] == 'RAW_INDEX']

df_bloom_pivot = df_bloom.pivot(index='tdate', columns='ticker', values='value')
df_bloom_pivot.index = [index for index in df_bloom_pivot.index]
empe.raw_index = empe.rename_columns(df_bloom_pivot, EmergingStrategy.BLOOM_EMERGING_COLUMNS)
empe.raw_index = empe.raw_index.resample("B").last()
empe.raw_index.index.name = 'tdate'
empe.raw_index.columns.name = 'ticker'


empe.set_rebalance_period(cs_freq='month', ts_freq='month')
empe.calculate_signal(CS=0.35, nopos=0.4, minobs1=12, minobs=60, IDN='out')
empe.set_portfolio_parameter(cs_strategy_type='notional')
empe.make_portfolio()

2020-02-07 17:30:45,287 - EMPE - INFO - [STEP 0] START LOGGING EMPE
2020-02-07 17:30:45,287 - EMPE - INFO - [STEP 0] START LOGGING EMPE
2020-02-07 17:30:45,290 - EMPE - INFO - [STEP 1] LOAD DATA
2020-02-07 17:30:45,290 - EMPE - INFO - [STEP 1] LOAD DATA
2020-02-07 17:30:45,291 - EMPE - INFO - [STEP 1 - 1] CONNECT TO BLOOM DATABASE
2020-02-07 17:30:45,291 - EMPE - INFO - [STEP 1 - 1] CONNECT TO BLOOM DATABASE
2020-02-07 17:30:45,294 - EMPE - INFO - [STEP 1 - 3] CHANGE BLOOM AND PAST DATA INTO STANDARD FORMAT
2020-02-07 17:30:45,294 - EMPE - INFO - [STEP 1 - 3] CHANGE BLOOM AND PAST DATA INTO STANDARD FORMAT
2020-02-07 17:30:47,396 - EMPE - INFO - [STEP 1 - 3] CHANGE BLOOM DATA INTO STANDARD FORMAT
2020-02-07 17:30:47,396 - EMPE - INFO - [STEP 1 - 3] CHANGE BLOOM DATA INTO STANDARD FORMAT
2020-02-07 17:30:49,310 - EMPE - INFO - [STEP 1 - 3] CHANGE BLOOM DATA INTO STANDARD FORMAT
2020-02-07 17:30:49,310 - EMPE - INFO - [STEP 1 - 3] CHANGE BLOOM DATA INTO STANDARD FORMAT
2020-02-07 17:31:0

In [18]:
start_date = '2006-01-01'
end_date = '2018-05-09'

# get r results
empe_comp_df = pd.read_csv('./past/empe.csv', header=0, index_col=0, parse_dates=True)
empe_lag_comp_df = pd.read_csv('./past/empe_lag.csv', header=0, index_col=0, parse_dates=True)

In [19]:
tester = Tester(empe)
tester.set_period(start=start_date, end=end_date)
tester.run(save_file=False, use_bt=False)

2020-02-07 17:32:28,294 - EMPE - INFO - [STEP 6] START BACKTEST
2020-02-07 17:32:28,294 - EMPE - INFO - [STEP 6] START BACKTEST
2020-02-07 17:32:28,295 - EMPE - INFO - [STEP 6 - 1] BACKTEST EMPE TIME SERIES
2020-02-07 17:32:28,295 - EMPE - INFO - [STEP 6 - 1] BACKTEST EMPE TIME SERIES
2020-02-07 17:32:29,094 - EMPE - INFO - [STEP 6 - 2] BACKTEST EMPE CROSS SECTIONAL
2020-02-07 17:32:29,094 - EMPE - INFO - [STEP 6 - 2] BACKTEST EMPE CROSS SECTIONAL


In [20]:
to_plot = (1.+ empe_lag_comp_df).loc[start_date:].cumprod()
to_plot['TS_python'] = tester.strategy.TS_result
to_plot['CS_python'] = tester.strategy.CS_result
to_plot.iplot()

# 3. EMPM

In [14]:
empm = EMPM(strategy_name="EMPM", asset_type="EMERGING")
empm.load_index_and_return(from_db=True, save_file=True)
empm.set_rebalance_period(ts_freq='month', cs_freq='week', rebalance_weekday=1)  # rebalance_day: monday = 0, sunday = 6
empm.calculate_signal(CS=0.35, minobs=260, minobs1=52, longlen1=52, longlen2=13, shortlen=2)
empm.set_portfolio_parameter(cs_strategy_type='notional')
empm.make_portfolio()

2020-01-21 10:03:53,221 - EMPM - INFO - [STEP 0] START LOGGING EMPM
2020-01-21 10:03:53,222 - EMPM - INFO - [STEP 1] LOAD DATA
2020-01-21 10:03:53,222 - EMPM - INFO - [STEP 1 - 1] CONNECT TO BLOOM DATABASE
2020-01-21 10:03:53,223 - EMPM - INFO - [STEP 1 - 3] CHANGE BLOOM AND PAST DATA INTO STANDARD FORMAT
2020-01-21 10:03:57,047 - EMPM - INFO - [STEP 1 - 3] CHANGE BLOOM DATA INTO STANDARD FORMAT
2020-01-21 10:04:01,237 - EMPM - INFO - [STEP 1 - 3] CHANGE BLOOM DATA INTO STANDARD FORMAT
2020-01-21 10:04:23,105 - EMPM - INFO - [STEP 1 - 4] MERGE BLOOM AND PAST DATA
2020-01-21 10:04:23,112 - EMPM - INFO - [STEP 1 - 5] SAVE RETURN DATA INTO CSV FORMAT
2020-01-21 10:04:23,285 - EMPM - INFO - [STEP 2] SET REBALANCE PERIOD
C:\Users\jungyoon.choi\Desktop\jungyoon\project\risk_premia\python\strategy\EMPM.py:70: FutureWarning:


Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https:/

In [15]:
start_date = '2006-01-01'
end_date = '2018-05-09'

# get r results
empm_comp_df = pd.read_csv('./past/empm.csv', header=0, index_col=0, parse_dates=True)
empm_lag_comp_df = pd.read_csv('./past/empm_lag.csv', header=0, index_col=0, parse_dates=True)

In [19]:
tester = Tester(empm)
tester.set_period(start=start_date, end=end_date)
tester.run(save_file=False, use_bt=False)

2020-01-21 10:09:40,138 - EMPM - INFO - [STEP 6] START BACKTEST
2020-01-21 10:09:40,139 - EMPM - INFO - [STEP 6 - 1] BACKTEST EMPM TIME SERIES
2020-01-21 10:09:41,233 - EMPM - INFO - [STEP 6 - 2] BACKTEST EMPM CROSS SECTIONAL


In [20]:
to_plot = (1.+ empm_lag_comp_df).loc[start_date:].cumprod()
to_plot['TS_python'] = tester.strategy.TS_result
to_plot['CS_python'] = tester.strategy.CS_result
to_plot.iplot()

# 4. EMSS

In [6]:
emss = EMSS(strategy_name="EMSS", asset_type="EMERGING")
emss.load_index_and_return(from_db=True, save_file=True)
emss.set_rebalance_period(ts_freq='month', cs_freq='month')  # rebalance_day: monday = 0, sunday = 6
emss.calculate_signal(CS=0.35, short=0.2, day1=24, fundwgt=1, statwgt=1, IDN='out')
emss.set_portfolio_parameter(cs_strategy_type="notional")
emss.make_portfolio()

2020-01-21 10:59:21,010 - EMSS - INFO - [STEP 0] START LOGGING EMSS
2020-01-21 10:59:21,013 - EMSS - INFO - [STEP 1] LOAD DATA
2020-01-21 10:59:21,013 - EMSS - INFO - [STEP 1 - 1] CONNECT TO BLOOM DATABASE
2020-01-21 10:59:21,023 - EMSS - INFO - [STEP 1 - 3] CHANGE BLOOM AND PAST DATA INTO STANDARD FORMAT
2020-01-21 10:59:24,933 - EMSS - INFO - [STEP 1 - 3] CHANGE BLOOM DATA INTO STANDARD FORMAT
2020-01-21 10:59:28,083 - EMSS - INFO - [STEP 1 - 3] CHANGE BLOOM DATA INTO STANDARD FORMAT
2020-01-21 10:59:45,966 - EMSS - INFO - [STEP 1 - 4] MERGE BLOOM AND PAST DATA
2020-01-21 10:59:45,973 - EMSS - INFO - [STEP 1 - 5] SAVE RETURN DATA INTO CSV FORMAT
2020-01-21 10:59:46,144 - EMSS - INFO - [STEP 2] SET REBALANCE PERIOD
2020-01-21 11:00:52,074 - EMSS - INFO - [STEP 4] SET PORTFOLIO PARAMETER
2020-01-21 11:00:52,075 - EMSS - INFO - [STEP 5] MAKE PORTFOLIO
2020-01-21 11:00:52,075 - EMSS - INFO - [STEP 5 - 1] CALCULATE VOLATILITY
2020-01-21 11:01:20,983 - EMSS - INFO - [STEP 5 - 2] MAKE TS PO

In [7]:
start_date = '2006-01-01'
end_date = '2018-05-09'

# get r results
emss_comp_df = pd.read_csv('./past/emss.csv', header=0, index_col=0, parse_dates=True)
emss_lag_comp_df = pd.read_csv('./past/emss_lag.csv', header=0, index_col=0, parse_dates=True)

In [8]:
tester = Tester(emss)
tester.set_period(start=start_date, end=end_date)
tester.run(save_file=False, use_bt=False)

2020-01-21 11:01:39,125 - EMSS - INFO - [STEP 6] START BACKTEST
2020-01-21 11:01:39,126 - EMSS - INFO - [STEP 6 - 1] BACKTEST EMSS TIME SERIES
2020-01-21 11:01:39,549 - EMSS - INFO - [STEP 6 - 2] BACKTEST EMSS CROSS SECTIONAL


In [9]:
to_plot = (1.+ emss_lag_comp_df).loc[start_date:].cumprod()
to_plot['TS_python'] = tester.strategy.TS_result
to_plot['CS_python'] = tester.strategy.CS_result
to_plot.iplot()

# 5. EMCA

In [21]:
emca = EMCA(strategy_name="EMCA", asset_type="EMERGING")
emca.load_index_and_return(from_db=True, save_file=True)
emca.load_strategy_data(table='bloom', origin='carry-em')

emca.set_rebalance_period(ts_freq='month', cs_freq='month')
emca.calculate_signal(CS=0.5, minobs1=12, nopos=0.4)
emca.set_portfolio_parameter(cs_strategy_type='notional')
emca.make_portfolio()

2020-01-21 10:10:18,234 - EMCA - INFO - [STEP 0] START LOGGING EMCA
2020-01-21 10:10:18,235 - EMCA - INFO - [STEP 1] LOAD DATA
2020-01-21 10:10:18,236 - EMCA - INFO - [STEP 1 - 1] CONNECT TO BLOOM DATABASE
2020-01-21 10:10:18,236 - EMCA - INFO - [STEP 1 - 3] CHANGE BLOOM AND PAST DATA INTO STANDARD FORMAT
2020-01-21 10:10:21,887 - EMCA - INFO - [STEP 1 - 3] CHANGE BLOOM DATA INTO STANDARD FORMAT
2020-01-21 10:10:23,994 - EMCA - INFO - [STEP 1 - 3] CHANGE BLOOM DATA INTO STANDARD FORMAT
2020-01-21 10:10:39,492 - EMCA - INFO - [STEP 1 - 4] MERGE BLOOM AND PAST DATA
2020-01-21 10:10:39,499 - EMCA - INFO - [STEP 1 - 5] SAVE RETURN DATA INTO CSV FORMAT
2020-01-21 10:10:44,917 - EMCA - INFO - [STEP 2] SET REBALANCE PERIOD
C:\Users\jungyoon.choi\Desktop\jungyoon\project\risk_premia\python\strategy\EMCA.py:37: FutureWarning:


Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https:/

In [22]:
start_date = '2008-01-01'
end_date = '2018-04-30'

# get r results
emca_comp_df = pd.read_csv('./past/emca.csv', header=0, index_col=0, parse_dates=True)
emca_lag_comp_df = pd.read_csv('./past/emca_lag.csv', header=0, index_col=0, parse_dates=True)

In [23]:
tester = Tester(emca)
tester.set_period(start=start_date, end=end_date)
tester.run(save_file=False, use_bt=False)

2020-01-21 10:11:50,168 - EMCA - INFO - [STEP 6] START BACKTEST
2020-01-21 10:11:50,168 - EMCA - INFO - [STEP 6 - 1] BACKTEST EMCA TIME SERIES
2020-01-21 10:11:50,532 - EMCA - INFO - [STEP 6 - 2] BACKTEST EMCA CROSS SECTIONAL


In [24]:
to_plot = (1.+ emca_lag_comp_df).loc[start_date:].cumprod()
to_plot['TS_python'] = tester.strategy.TS_result
to_plot['CS_python'] = tester.strategy.CS_result
to_plot.iplot()